In [1]:
# upgrading pip file
try:
  import colab
  !pip install --upgrade pip
except:
  pass

In [2]:
#installing tfdv
print('Installing TensorFlow Data Validation')
!pip install --upgrade 'tensorflow_data_validation[visualization]<2'

Installing TensorFlow Data Validation
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 19.1/19.1 MB 61.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.8/14.8 MB 75.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 35.9/35.9 MB 10.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 99.9/99.9 kB 14.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 22.5/22.5 MB 56.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 89.7/89.7 kB 13.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 138.5/138.5 kB 16.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 152.0/152.0 kB 18.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 40.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.5/43.5 kB 5.1 MB/s eta 0:00:00
  Preparing metadata (setup.

In [3]:
#importing packages
import pkg_resources
import importlib
importlib.reload(pkg_resources)

<module 'pkg_resources' from '/usr/local/lib/python3.10/dist-packages/pkg_resources/__init__.py'>

In [4]:
#checking tfdv versions
import tensorflow as tf
import tensorflow_data_validation as tfdv
print('TF version:', tf.__version__)
print('TFDV version:', tfdv.version.__version__)

TF version: 2.15.0
TFDV version: 1.14.0


In [5]:
#reading json input file
import json

# Path to your JSON file
file_path = '/content/train.json'

# Open the JSON file
with open(file_path) as f:
    data = json.load(f)

# Now 'data' contains the content of your JSON file


In [6]:
# converting json data to TFrecord
import json
import tensorflow as tf

# Function to convert JSON data to TFRecord
def json_to_tfrecord(json_data):
    feature = {
        "document": tf.train.Feature(int64_list=tf.train.Int64List(value=[json_data["document"]])),
        "full_text": tf.train.Feature(bytes_list=tf.train.BytesList(value=[json_data["full_text"].encode("utf-8")])),
        "tokens": tf.train.Feature(bytes_list=tf.train.BytesList(value=[tf.compat.as_bytes(token) for token in json_data["tokens"]])),
        "trailing_whitespace": tf.train.Feature(int64_list=tf.train.Int64List(value=[int(ws) for ws in json_data["trailing_whitespace"]])),
    }

    if "labels" in json_data:
        feature["labels"] = tf.train.Feature(bytes_list=tf.train.BytesList(value=[tf.compat.as_bytes(label) for label in json_data["labels"]]))

    example_proto = tf.train.Example(features=tf.train.Features(feature=feature))
    return example_proto.SerializeToString()

# Path to your JSON file in Google Drive
json_file_path = '/content/train.json'

# Write TFRecord file
tfrecord_file_path = '/content/output.tfrecord'
with tf.io.TFRecordWriter(tfrecord_file_path) as writer:
    with open(json_file_path) as json_file:
        data = json.load(json_file)
        for item in data:
            example = json_to_tfrecord(item)
            writer.write(example)


In [7]:
import tensorflow_data_validation as tfdv

# Path to your TFRecord file in Google Drive
tfrecord_file_path = '/content/output.tfrecord'

# Generate statistics
stats = tfdv.generate_statistics_from_tfrecord(tfrecord_file_path)

# Visualize statistics
tfdv.visualize_statistics(stats)


Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


In [8]:
# Infer schema
schema = tfdv.infer_schema(stats)

# Display schema
tfdv.display_schema(schema)

Type  Presence  Valency    Domain
Feature name                                              
'document'                INT  required                  -
'full_text'             BYTES  required                  -
'labels'               STRING  required  [1,inf)  'labels'
'tokens'                BYTES  required  [1,inf)         -
'trailing_whitespace'     INT  required  [1,inf)         -

Values
Domain                                                                                                                                                                                                      
'labels'  'B-EMAIL', 'B-ID_NUM', 'B-NAME_STUDENT', 'B-PHONE_NUM', 'B-STREET_ADDRESS', 'B-URL_PERSONAL', 'B-USERNAME', 'I-ID_NUM', 'I-NAME_STUDENT', 'I-PHONE_NUM', 'I-STREET_ADDRESS', 'I-URL_PERSONAL', 'O'